In [1]:
!pip install git+https://github.com/cosmo3769/diffusers@standardize-model-card-template-t2i-adapter-sdxl -q

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [4]:
import os
from PIL import Image
from diffusers.utils.hub_utils import load_or_create_model_card, populate_model_card

In [5]:
def image_grid(imgs, rows, cols):
    assert len(imgs) == rows * cols

    w, h = imgs[0].size
    grid = Image.new("RGB", size=(cols * w, rows * h))

    for i, img in enumerate(imgs):
        grid.paste(img, box=(i % cols * w, i // cols * h))
    return grid

In [6]:
def save_model_card(repo_id: str, image_logs: dict = None, base_model: str = None, repo_folder: str = None):
    img_str = ""
    if image_logs is not None:
        img_str = "You can find some example images below.\n"
        for i, log in enumerate(image_logs):
            images = log["images"]
            validation_prompt = log["validation_prompt"]
            validation_image = log["validation_image"]
            validation_image.save(os.path.join(repo_folder, "image_control.png"))
            img_str += f"prompt: {validation_prompt}\n"
            images = [validation_image] + images
            image_grid(images, 1, len(images)).save(os.path.join(repo_folder, f"images_{i}.png"))
            img_str += f"![images_{i})](./images_{i}.png)\n"

    model_description = f"""
# t2iadapter-{repo_id}

These are t2iadapter weights trained on {base_model} with new type of conditioning.
{img_str}
"""
    model_card = load_or_create_model_card(
        repo_id_or_path=repo_id,
        from_training=True,
        license="creativeml-openrail-m",
        base_model=base_model,
        model_description=model_description,
        inference=True,
    )

    tags = ["stable-diffusion-xl", "stable-diffusion-xl-diffusers", "text-to-image", "diffusers", "t2iadapter"]
    model_card = populate_model_card(model_card, tags=tags)

    model_card.save(os.path.join(repo_folder, "README.md"))

In [7]:
from diffusers.utils import load_image

images = [
    load_image("https://huggingface.co/datasets/diffusers/docs-images/resolve/main/amused/A%20mushroom%20in%20%5BV%5D%20style.png")
    for _ in range(3)
]

image_logs = [
    dict(
        images=[image],
        validation_prompt="validation_prompt",
        validation_image=image,
    )
    for image in images
]

save_model_card(
    repo_id="cosmo3769/t2i-adapter-sdxl",
    image_logs=image_logs,
    base_model="runwayml/stable-diffusion-v1-5",
    repo_folder=".",
)

In [8]:
!cat README.md

---
license: creativeml-openrail-m
library_name: diffusers
tags:
- stable-diffusion-xl
- stable-diffusion-xl-diffusers
- text-to-image
- diffusers
- t2iadapter
inference: true
base_model: runwayml/stable-diffusion-v1-5
---

<!-- This model card has been generated automatically according to the information the training script had access to. You
should probably proofread and complete it, then remove this comment. -->


# t2iadapter-cosmo3769/t2i-adapter-sdxl

These are t2iadapter weights trained on runwayml/stable-diffusion-v1-5 with new type of conditioning.
You can find some example images below.
prompt: validation_prompt
![images_0)](./images_0.png)
prompt: validation_prompt
![images_1)](./images_1.png)
prompt: validation_prompt
![images_2)](./images_2.png)



## Intended uses & limitations

#### How to use

```python
# TODO: add an example code snippet for running this diffusion pipeline
```

#### Limitations and bias

[TODO: provide examples of latent issues and potential remediatio